## Notebook from machine-learning-with-ontologies

In [1]:
import click as ck
import numpy as np
import pandas as pd
import tensorflow as tf
from tensorflow.python.framework import function
import re
import math
import matplotlib.pyplot as plt
import logging
from tensorflow.keras.layers import (
    Input,
)
from tensorflow.keras import optimizers
from tensorflow.keras import constraints
from tensorflow.keras.callbacks import ModelCheckpoint, EarlyStopping, CSVLogger
from tensorflow.keras import backend as K
from scipy.stats import rankdata
import os

from elembeddings.elembedding import (
    ELModel, load_data, load_valid_data, Generator, MyModelCheckpoint)



2022-06-10 10:26:18.306947: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-06-10 10:26:18.307002: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.


AttributeError: module 'tensorflow' has no attribute 'ConfigProto'

### Set parameters

In [9]:
# Parameters
batch_size = 256
embedding_size = 50
margin = -0.1
reg_norm = 1
learning_rate = 1e-3
epochs = 20
org_id = '9606'

### Load training and validation data

In [8]:
# Load training data in (h, l, t) triples
# classes and relations are entity to id mappings
train_data, classes, relations = load_data(f'data/train/{org_id}.classes-normalized.owl')
valid_data = load_valid_data(f'data/valid/{org_id}.protein.links.v11.0.txt', classes, relations)
for key, value in train_data.items():
    print(f'{key} {len(value)}')
for key, value in classes.items():
    print(f'{key}: {value}')
for key, value in relations.items():
    print(f'{key}: {value}')
for h, l, t in valid_data:
    print(f'{h}: {l}: {t}')

nf1 85119
nf2 12090
nf3 749275
nf4 12088
disjoint 30
nf3_neg 1076572
top 1
<http://9606.ENSP00000380153>: 0
<http://9606.ENSP00000345374>: 1
<http://purl.obolibrary.org/obo/GO_0034868>: 2
<http://purl.obolibrary.org/obo/GO_0016614>: 3
<http://9606.ENSP00000300659>: 4
<http://9606.ENSP00000360266>: 5
<http://9606.ENSP00000438788>: 6
<http://9606.ENSP00000379025>: 7
<http://9606.ENSP00000325425>: 8
<http://9606.ENSP00000264198>: 9
<http://9606.ENSP00000317872>: 10
<http://9606.ENSP00000264658>: 11
<http://9606.ENSP00000268711>: 12
<http://9606.ENSP00000263253>: 13
<http://purl.obolibrary.org/obo/GO_0034863>: 14
<http://9606.ENSP00000299601>: 15
<http://9606.ENSP00000373772>: 16
<http://9606.ENSP00000281871>: 17
<http://9606.ENSP00000369871>: 18
<http://9606.ENSP00000167586>: 19
<http://purl.obolibrary.org/obo/GO_0042633>: 20
<http://9606.ENSP00000299424>: 21
<http://purl.obolibrary.org/obo/GO_0006367>: 22
<http://9606.ENSP00000369055>: 23
<http://9606.ENSP00000377257>: 24
<http://9606.EN

<http://purl.obolibrary.org/obo/GO_0035922>: 2852
<http://purl.obolibrary.org/obo/GO_0033300>: 2853
<http://purl.obolibrary.org/obo/GO_0070837>: 2854
<http://9606.ENSP00000336528>: 2855
<http://9606.ENSP00000340900>: 2856
<http://9606.ENSP00000303634>: 2857
<http://9606.ENSP00000263816>: 2858
<http://9606.ENSP00000225844>: 2859
<http://9606.ENSP00000384018>: 2860
<http://9606.ENSP00000258042>: 2861
<http://9606.ENSP00000255192>: 2862
<http://purl.obolibrary.org/obo/GO_0033477>: 2863
<http://9606.ENSP00000296435>: 2864
<http://9606.ENSP00000455106>: 2865
<http://9606.ENSP00000378323>: 2866
<http://purl.obolibrary.org/obo/GO_0097002>: 2867
<http://purl.obolibrary.org/obo/GO_0034724>: 2868
<http://purl.obolibrary.org/obo/GO_0034723>: 2869
<http://9606.ENSP00000379396>: 2870
<http://9606.ENSP00000444736>: 2871
<http://purl.obolibrary.org/obo/GO_0015015>: 2872
<http://9606.ENSP00000378286>: 2873
<http://9606.ENSP00000226105>: 2874
<http://9606.ENSP00000378289>: 2875
<http://9606.ENSP0000035

<http://9606.ENSP00000405068>: 3324
<http://9606.ENSP00000364404>: 3325
<http://9606.ENSP00000385451>: 3326
<http://9606.ENSP00000303706>: 3327
<http://9606.ENSP00000441235>: 3328
<http://9606.ENSP00000312470>: 3329
<http://9606.ENSP00000274311>: 3330
<http://9606.ENSP00000314004>: 3331
<http://9606.ENSP00000265773>: 3332
<http://purl.obolibrary.org/obo/GO_0000073>: 3333
<http://purl.obolibrary.org/obo/GO_0110100>: 3334
<http://9606.ENSP00000334002>: 3335
<http://purl.obolibrary.org/obo/GO_0032901>: 3336
<http://9606.ENSP00000353512>: 3337
<http://9606.ENSP00000297423>: 3338
<http://9606.ENSP00000364813>: 3339
<http://9606.ENSP00000354995>: 3340
<http://9606.ENSP00000355568>: 3341
<http://purl.obolibrary.org/obo/GO_0004666>: 3342
<http://9606.ENSP00000262304>: 3343
<http://9606.ENSP00000296545>: 3344
<http://9606.ENSP00000262300>: 3345
<http://9606.ENSP00000392466>: 3346
<http://9606.ENSP00000345206>: 3347
<http://purl.obolibrary.org/obo/GO_0018510>: 3348
<http://9606.ENSP00000298746>:

<http://9606.ENSP00000391490>: 6491
<http://purl.obolibrary.org/obo/GO_1903896>: 6492
<http://9606.ENSP00000234677>: 6493
<http://9606.ENSP00000364802>: 6494
<http://9606.ENSP00000350815>: 6495
<http://9606.ENSP00000398722>: 6496
<http://9606.ENSP00000345968>: 6497
<http://9606.ENSP00000420298>: 6498
<http://9606.ENSP00000375629>: 6499
<http://9606.ENSP00000386456>: 6500
<http://purl.obolibrary.org/obo/GO_0097141>: 6501
<http://purl.obolibrary.org/obo/GO_0097136>: 6502
<http://9606.ENSP00000380227>: 6503
<http://purl.obolibrary.org/obo/GO_0034760>: 6504
<http://9606.ENSP00000392028>: 6505
<http://purl.obolibrary.org/obo/GO_0097144>: 6506
<http://9606.ENSP00000367794>: 6507
<http://9606.ENSP00000331209>: 6508
<http://9606.ENSP00000236877>: 6509
<http://purl.obolibrary.org/obo/GO_0036446>: 6510
<http://purl.obolibrary.org/obo/GO_0036308>: 6511
<http://purl.obolibrary.org/obo/GO_0034761>: 6512
<http://9606.ENSP00000379612>: 6513
<http://9606.ENSP00000296861>: 6514
<http://9606.ENSP0000026

<http://purl.obolibrary.org/obo/GO_0102460>: 10123
<http://9606.ENSP00000478892>: 10124
<http://purl.obolibrary.org/obo/GO_0102458>: 10125
<http://purl.obolibrary.org/obo/GO_0102457>: 10126
<http://purl.obolibrary.org/obo/GO_0102456>: 10127
<http://purl.obolibrary.org/obo/GO_0102455>: 10128
<http://9606.ENSP00000359904>: 10129
<http://9606.ENSP00000263182>: 10130
<http://9606.ENSP00000344411>: 10131
<http://purl.obolibrary.org/obo/GO_0033031>: 10132
<http://purl.obolibrary.org/obo/GO_0001781>: 10133
<http://9606.ENSP00000273075>: 10134
<http://9606.ENSP00000287647>: 10135
<http://9606.ENSP00000334187>: 10136
<http://9606.ENSP00000316737>: 10137
<http://purl.obolibrary.org/obo/GO_0102301>: 10138
<http://9606.ENSP00000355013>: 10139
<http://9606.ENSP00000037243>: 10140
<http://9606.ENSP00000483721>: 10141
<http://purl.obolibrary.org/obo/GO_0033030>: 10142
<http://9606.ENSP00000302100>: 10143
<http://purl.obolibrary.org/obo/GO_0003887>: 10144
<http://purl.obolibrary.org/obo/GO_0002565>: 1

...

8190: 0: 3873
3873: 0: 8190
9692: 0: 495
495: 0: 9692
17446: 0: 14046
14046: 0: 17446
4857: 0: 580
580: 0: 4857
5: 0: 4667
4667: 0: 5
4749: 0: 18
18: 0: 4749
3558: 0: 241
241: 0: 3558
7493: 0: 1107
1107: 0: 7493
20141: 0: 4621
4621: 0: 20141
8440: 0: 3247
3247: 0: 8440
161: 0: 4422
4422: 0: 161
10877: 0: 24616
24616: 0: 10877
4878: 0: 2935
2935: 0: 4878
35053: 0: 28224
28224: 0: 35053
4956: 0: 1520
1520: 0: 4956
4525: 0: 9767
9767: 0: 4525
988: 0: 1392
1392: 0: 988
7150: 0: 9332
9332: 0: 7150
4013: 0: 1047
1047: 0: 4013
16981: 0: 647
647: 0: 16981
22700: 0: 982
982: 0: 22700
1179: 0: 6086
6086: 0: 1179
4875: 0: 325
325: 0: 4875
15227: 0: 4428
4428: 0: 15227
1247: 0: 150
150: 0: 1247
8241: 0: 19346
19346: 0: 8241
8878: 0: 20341
20341: 0: 8878
1392: 0: 5220
5220: 0: 1392
3221: 0: 4382
4382: 0: 3221
1751: 0: 9164
9164: 0: 1751
1848: 0: 19518
19518: 0: 1848
1187: 0: 442
442: 0: 1187
8879: 0: 10938
10938: 0: 8879
7327: 0: 2413
2413: 0: 7327
1000: 0: 3165
3165: 0: 1000
2947: 0: 2666
2666: 0:

7114: 0: 28224
28224: 0: 7114
3045: 0: 2139
2139: 0: 3045
4155: 0: 984
984: 0: 4155
275: 0: 3911
3911: 0: 275
5780: 0: 231
231: 0: 5780
4383: 0: 326
326: 0: 4383
21213: 0: 24106
24106: 0: 21213
5120: 0: 3552
3552: 0: 5120
12654: 0: 13141
13141: 0: 12654
3215: 0: 14545
14545: 0: 3215
6218: 0: 11071
11071: 0: 6218
20807: 0: 8752
8752: 0: 20807
1603: 0: 6228
6228: 0: 1603
22933: 0: 41110
41110: 0: 22933
8061: 0: 49
49: 0: 8061
1799: 0: 1318
1318: 0: 1799
11743: 0: 2848
2848: 0: 11743
8773: 0: 5693
5693: 0: 8773
2056: 0: 7071
7071: 0: 2056
3913: 0: 4585
4585: 0: 3913
6927: 0: 721
721: 0: 6927
4992: 0: 1266
1266: 0: 4992
6957: 0: 4437
4437: 0: 6957
2055: 0: 628
628: 0: 2055
4437: 0: 4697
4697: 0: 4437
14583: 0: 2709
2709: 0: 14583
662: 0: 1098
1098: 0: 662
264: 0: 13500
13500: 0: 264
1598: 0: 2124
2124: 0: 1598
547: 0: 2657
2657: 0: 547
3486: 0: 52
52: 0: 3486
3291: 0: 2342
2342: 0: 3291
1534: 0: 869
869: 0: 1534
1336: 0: 2957
2957: 0: 1336
9240: 0: 21320
21320: 0: 9240
502: 0: 10059
10059:

25318: 0: 241
241: 0: 25318
10941: 0: 3837
3837: 0: 10941
777: 0: 397
397: 0: 777
1346: 0: 1644
1644: 0: 1346
544: 0: 644
644: 0: 544
7161: 0: 7663
7663: 0: 7161
1489: 0: 1974
1974: 0: 1489
3054: 0: 4616
4616: 0: 3054
183: 0: 458
458: 0: 183
8499: 0: 10562
10562: 0: 8499
2723: 0: 12491
12491: 0: 2723
760: 0: 5639
5639: 0: 760
3651: 0: 4069
4069: 0: 3651
325: 0: 18584
18584: 0: 325
29065: 0: 25496
25496: 0: 29065
2079: 0: 1671
1671: 0: 2079
372: 0: 12093
12093: 0: 372
13394: 0: 22767
22767: 0: 13394
5892: 0: 47154
47154: 0: 5892
2305: 0: 13671
13671: 0: 2305
914: 0: 6992
6992: 0: 914
12025: 0: 28127
28127: 0: 12025
12453: 0: 3494
3494: 0: 12453
7763: 0: 23958
23958: 0: 7763
4703: 0: 11561
11561: 0: 4703
2723: 0: 10331
10331: 0: 2723
6965: 0: 12294
12294: 0: 6965
7547: 0: 2230
2230: 0: 7547
19435: 0: 6370
6370: 0: 19435
6203: 0: 614
614: 0: 6203
713: 0: 1181
1181: 0: 713
10118: 0: 8808
8808: 0: 10118
2625: 0: 5699
5699: 0: 2625
1969: 0: 1340
1340: 0: 1969
1532: 0: 111
111: 0: 1532
3372: 

4388: 0: 9457
9457: 0: 4388
5706: 0: 6801
6801: 0: 5706
1985: 0: 6125
6125: 0: 1985
26840: 0: 39921
39921: 0: 26840
4039: 0: 4838
4838: 0: 4039
5126: 0: 9055
9055: 0: 5126
3459: 0: 8795
8795: 0: 3459
3128: 0: 5639
5639: 0: 3128
1032: 0: 8922
8922: 0: 1032
6541: 0: 2079
2079: 0: 6541
481: 0: 9434
9434: 0: 481
1285: 0: 3794
3794: 0: 1285
484: 0: 545
545: 0: 484
1570: 0: 11005
11005: 0: 1570
15164: 0: 5301
5301: 0: 15164
8701: 0: 1846
1846: 0: 8701
350: 0: 1204
1204: 0: 350
6130: 0: 3499
3499: 0: 6130
964: 0: 2779
2779: 0: 964
5957: 0: 2475
2475: 0: 5957
2543: 0: 1782
1782: 0: 2543
6707: 0: 2871
2871: 0: 6707
918: 0: 6830
6830: 0: 918
4703: 0: 5071
5071: 0: 4703
3167: 0: 852
852: 0: 3167
3440: 0: 8429
8429: 0: 3440
2125: 0: 3294
3294: 0: 2125
4542: 0: 14725
14725: 0: 4542
6614: 0: 647
647: 0: 6614
270: 0: 5480
5480: 0: 270
28039: 0: 4175
4175: 0: 28039
23699: 0: 8217
8217: 0: 23699
16216: 0: 35316
35316: 0: 16216
20497: 0: 22470
22470: 0: 20497
1396: 0: 12584
12584: 0: 1396
30050: 0: 8391

11: 0: 464
464: 0: 11
11879: 0: 2952
2952: 0: 11879
8196: 0: 6791
6791: 0: 8196
183: 0: 1613
1613: 0: 183
3465: 0: 22732
22732: 0: 3465
6219: 0: 36247
36247: 0: 6219
3017: 0: 3288
3288: 0: 3017
3811: 0: 9378
9378: 0: 3811
13643: 0: 8317
8317: 0: 13643
3676: 0: 2776
2776: 0: 3676
3187: 0: 1088
1088: 0: 3187
7723: 0: 1363
1363: 0: 7723
2972: 0: 24843
24843: 0: 2972
2893: 0: 18576
18576: 0: 2893
952: 0: 3651
3651: 0: 952
6470: 0: 9814
9814: 0: 6470
18160: 0: 19044
19044: 0: 18160
3291: 0: 11136
11136: 0: 3291
2362: 0: 12833
12833: 0: 2362
7630: 0: 4407
4407: 0: 7630
9165: 0: 7506
7506: 0: 9165
1480: 0: 2163
2163: 0: 1480
9240: 0: 9703
9703: 0: 9240
6130: 0: 12602
12602: 0: 6130
3873: 0: 3943
3943: 0: 3873
4896: 0: 3158
3158: 0: 4896
6107: 0: 1344
1344: 0: 6107
3045: 0: 2792
2792: 0: 3045
2264: 0: 32688
32688: 0: 2264
12849: 0: 1495
1495: 0: 12849
12791: 0: 1527
1527: 0: 12791
201: 0: 11658
11658: 0: 201
10534: 0: 3537
3537: 0: 10534
12876: 0: 5170
5170: 0: 12876
4245: 0: 5799
5799: 0: 424

In [10]:
# Filter out protein classes
proteins = {}
for k, v in classes.items():
    if not k.startswith('<http://purl.obolibrary.org/obo/GO_'):
        proteins[k] = v

# Prepare data for training the model
nb_classes = len(classes)
nb_relations = len(relations)
nb_train_data = 0
for key, val in train_data.items():
    nb_train_data = max(len(val), nb_train_data)
train_steps = int(math.ceil(nb_train_data / (1.0 * batch_size)))
train_generator = Generator(train_data, batch_size, steps=train_steps)

# id to entity maps
cls_dict = {v: k for k, v in classes.items()}
rel_dict = {v: k for k, v in relations.items()}

cls_list = []
rel_list = []
for i in range(nb_classes):
    cls_list.append(cls_dict[i])
for i in range(nb_relations):
    rel_list.append(rel_dict[i])

        
print('Total number of classes', nb_classes)
print('Total number of relations', nb_relations)

Total number of classes 61810
Total number of relations 10


### Build ELEmbeddings Model and Train

Embeddings are saved depending on mean rank evaluation on validation set

In [11]:
# Input layers for each loss type
nf1 = Input(shape=(2,), dtype=np.int32)
nf2 = Input(shape=(3,), dtype=np.int32)
nf3 = Input(shape=(3,), dtype=np.int32)
nf4 = Input(shape=(3,), dtype=np.int32)
dis = Input(shape=(3,), dtype=np.int32)
top = Input(shape=(1,), dtype=np.int32)
nf3_neg = Input(shape=(3,), dtype=np.int32)

# Build model
el_model = ELModel(nb_classes, nb_relations, embedding_size, batch_size, margin, reg_norm)
out = el_model([nf1, nf2, nf3, nf4, dis, top, nf3_neg])
model = tf.keras.Model(inputs=[nf1, nf2, nf3, nf4, dis, top, nf3_neg], outputs=out)
optimizer = optimizers.Adam(lr=learning_rate)
model.compile(optimizer=optimizer, loss='mse')

# Pandas files to store embeddings
if not os.path.exists('data/elembeddings'):
    os.makedirs('data/elembeddings')
out_classes_file = f'data/elembeddings/{org_id}_cls_embeddings.pkl'
out_relations_file = f'data/elembeddings/{org_id}_rel_embeddings.pkl'

# ModelCheckpoint which runs at the end of each epoch
checkpointer = MyModelCheckpoint(
    out_classes_file=out_classes_file,
    out_relations_file=out_relations_file,
    cls_list=cls_list,
    rel_list=rel_list,
    valid_data=valid_data,
    proteins=proteins,
    monitor='loss')

# Start training
model.fit_generator(
    train_generator,
    steps_per_epoch=train_steps,
    epochs=epochs,
    workers=12,
    callbacks=[checkpointer,])


/home/leopold/Documents/4A/stage/machine-learning-with-ontologies/ml_ontologies/lib/python3.6/site-packages/tensorflow/python/ops/gradients_impl.py:112: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Epoch 1/10
4204/4206 [============================>.] - ETA: 0s - loss: 34.1288
 Validation 1 8020.622255235073


 Saving embeddings 1 8020.622255235073

4206/4206 [==============================] - 589s 140ms/step - loss: 34.1269
Epoch 2/10
4205/4206 [============================>.] - ETA: 0s - loss: 28.1475
 Validation 2 8102.071004655061

4206/4206 [==============================] - 610s 145ms/step - loss: 28.1469
Epoch 3/10
4202/4206 [============================>.] - ETA: 0s - loss: 24.4798
 Validation 3 8130.537704500891

4206/4206 [==============================] - 551s 131ms/step - loss: 24.4782
Epoch 4/10
4204/4206 [============================>.] - ETA: 0s - loss: 21.6699
 Validation 4 8120.132669251148

4206/4206 [==============================] - 534s 127ms/step - loss: 21.6693
Epoch 5/10
4205/4206 [============================>.] - ETA: 0s - loss: 19.4163
 Validation 5 8085.232341451002

4206/4206 [==============================] - 509s 121ms/step - loss: 19.4159
Epoch 6/1

### Evaluation of embeddings on the test set

In [12]:
def load_test_data(data_file, classes, relations):
    data = []
    rel = f'<http://interacts>'
    with open(data_file, 'r') as f:
        for line in f:
            it = line.strip().split()
            id1 = f'<http://{it[0]}>'
            id2 = f'<http://{it[1]}>'
            if id1 not in classes or id2 not in classes or rel not in relations:
                continue
            data.append((id1, rel, id2))
    return data

def compute_rank_roc(ranks, n_prots):
    auc_x = list(ranks.keys())
    auc_x.sort()
    auc_y = []
    tpr = 0
    sum_rank = sum(ranks.values())
    for x in auc_x:
        tpr += ranks[x]
        auc_y.append(tpr / sum_rank)
    auc_x.append(n_prots)
    auc_y.append(1)
    auc = np.trapz(auc_y, auc_x) / n_prots
    return auc


# Pandas files to store embeddings
out_classes_file = f'data/elembeddings/{org_id}_cls_embeddings.pkl'
out_relations_file = f'data/elembeddings/{org_id}_rel_embeddings.pkl'

cls_df = pd.read_pickle(out_classes_file)
rel_df = pd.read_pickle(out_relations_file)
nb_classes = len(cls_df)
nb_relations = len(rel_df)
embeds_list = cls_df['embeddings'].values
rembeds_list = rel_df['embeddings'].values
size = len(embeds_list[0])
embeds = np.zeros((nb_classes, size), dtype=np.float32)
for i, emb in enumerate(embeds_list):
    embeds[i, :] = emb

rs = np.abs(embeds[:, -1]).reshape(-1, 1)
embeds = embeds[:, :-1]
prot_index = list(proteins.values())
prot_rs = rs[prot_index, :]
prot_embeds = embeds[prot_index, :]
prot_dict = {v: k for k, v in enumerate(prot_index)}
    
rsize = len(rembeds_list[0])
rembeds = np.zeros((nb_relations, rsize), dtype=np.float32)
for i, emb in enumerate(rembeds_list):
    rembeds[i, :] = emb

train_data = load_test_data(f'data/train/{org_id}.protein.links.v11.0.txt', classes, relations)
valid_data = load_test_data(f'data/valid/{org_id}.protein.links.v11.0.txt', classes, relations)
trlabels = {}
for c, r, d in train_data:
    c, r, d = prot_dict[classes[c]], relations[r], prot_dict[classes[d]]
    if r not in trlabels:
        trlabels[r] = np.ones((len(prot_embeds), len(prot_embeds)), dtype=np.int32)
    trlabels[r][c, d] = 1000
for c, r, d in valid_data:
    c, r, d = prot_dict[classes[c]], relations[r], prot_dict[classes[d]]
    if r not in trlabels:
        trlabels[r] = np.ones((len(prot_embeds), len(prot_embeds)), dtype=np.int32)
    trlabels[r][c, d] = 1000

test_data = load_test_data(f'data/test/{org_id}.protein.links.v11.0.txt', classes, relations)
top1 = 0
top10 = 0
top100 = 0
mean_rank = 0
ftop1 = 0
ftop10 = 0
ftop100 = 0
fmean_rank = 0
labels = {}
preds = {}
ranks = {}
franks = {}
eval_data = test_data
n = len(eval_data)
for c, r, d in eval_data:
    c, r, d = prot_dict[classes[c]], relations[r], prot_dict[classes[d]]
    if r not in labels:
        labels[r] = np.zeros((len(prot_embeds), len(prot_embeds)), dtype=np.int32)
    if r not in preds:
        preds[r] = np.zeros((len(prot_embeds), len(prot_embeds)), dtype=np.float32)
    labels[r][c, d] = 1
    ec = prot_embeds[c, :]
    rc = prot_rs[c, :]
    er = rembeds[r, :]
    ec += er

    # Compute similarity
    dst = np.linalg.norm(prot_embeds - ec.reshape(1, -1), axis=1)
    dst = dst.reshape(-1, 1)
    res = np.maximum(0, dst - rc - prot_rs - margin)
    res = res.flatten()

    preds[r][c, :] = res
    index = rankdata(res, method='average')
    rank = index[d]
    if rank == 1:
        top1 += 1
    if rank <= 10:
        top10 += 1
    if rank <= 100:
        top100 += 1
    mean_rank += rank
    if rank not in ranks:
        ranks[rank] = 0
    ranks[rank] += 1

    # Filtered rank
    index = rankdata((res * trlabels[r][c, :]), method='average')
    rank = index[d]
    if rank == 1:
        ftop1 += 1
    if rank <= 10:
        ftop10 += 1
    if rank <= 100:
        ftop100 += 1
    fmean_rank += rank

    if rank not in franks:
        franks[rank] = 0
    franks[rank] += 1
top1 /= n
top10 /= n
top100 /= n
mean_rank /= n
ftop1 /= n
ftop10 /= n
ftop100 /= n
fmean_rank /= n

rank_auc = compute_rank_roc(ranks, len(proteins))
frank_auc = compute_rank_roc(franks, len(proteins))

print(f'Evaluation for {org_id}')
print(f'{top10:.2f} {top100:.2f} {mean_rank:.2f} {rank_auc:.2f}')
print(f'{ftop10:.2f} {ftop100:.2f} {fmean_rank:.2f} {frank_auc:.2f}')

Evaluation for 9606
0.00 0.01 7881.01 0.52
0.00 0.01 7809.84 0.52
